In [1]:
# !pip install altair 
# !pip install altair_saver
# !npm install -g vega-lite vega-cli canvas
# !pip install vl-convert-python

In [2]:
# !apt update
# !apt install ttf-mscorefonts-installer -y
# !apt reinstall fontconfig fontconfig-config libfontconfig1 -y

In [3]:
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Black.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Bold.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Book.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Medium.otf -P /usr/local/share/fonts

In [4]:
# !fc-cache -f

In [5]:
import json
import altair as alt
from altair import expr, datum
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests
import urllib.parse

In [6]:
import colorsys
from matplotlib.colors import to_hex, to_rgb


def scale_lightness(rgb, scale_l):
    rgbhex = False
    if "#" in rgb:
        rgb = to_rgb(rgb)
        rgbhex = True
    # convert rgb to hls
    h, l, s = colorsys.rgb_to_hls(*rgb)
    # manipulate h, l, s values and return as rgb
    c = colorsys.hls_to_rgb(h, min(1, l * scale_l), s=s)
    if rgbhex:
        c = to_hex(c)
    return c

In [7]:
SAVE = False
LOCAL = True
DARK = True

if LOCAL:
    local_suffix = "" #_local
else:
    local_suffix = ""

In [8]:
%%capture pwd
!pwd

In [9]:
uid = pwd.stdout.split("/")[-1].split("\r")[0]
uid=urllib.parse.quote(uid)
eco_git_home = (
    "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/"
)
eco_git_path = eco_git_home + "magazine/" + uid + "/data/"
vega_embed = requests.get(eco_git_home + "guidelines/html/vega-embed.html").text
colors = json.loads(
    requests.get(eco_git_home + "guidelines/colors/eco-colors.json").content
)
category_color = json.loads(
    requests.get(eco_git_home + "guidelines/colors/eco-category-color.json").content
)
hue_color = json.loads(
    requests.get(eco_git_home + "guidelines/colors/eco-single-hue-color.json").content
)
mhue_color = json.loads(
    requests.get(eco_git_home + "guidelines/colors/eco-multi-hue-color.json").content
)
div_color = json.loads(
    requests.get(eco_git_home + "guidelines/colors/eco-diverging-color.json").content
)
config = json.loads(
    requests.get(eco_git_home + "guidelines/charts/eco-global-config.json").content
)
mo=0.5
mo0=0.01
height = config["height"]
width = config["width"]
uid, height, width

('issue-3', 300, 500)

In [10]:
def save(df, f, LOCAL):
    fc = eco_git_path + f + ".csv"
    df.to_csv("data/" + f + ".csv")
    f += local_suffix
    open("visualisation/" + f + ".html", "w").write(
        vega_embed.replace(
            "JSON_PATH", fc.replace("/data/", "/visualisation/").replace(".csv", ".json")
        )
    )
    if LOCAL:
        fc = df
    
    from IPython.display import display, HTML
    display(HTML(df.head().to_html()))
    
    # readme = "## Figure " + f.replace('fig','').split('_')[0] + \
    
    readme = "## Figure " + f.replace('fig','').split('_')[0] + \
        '  \n\nData: [`csv`](data/' + f + '.csv)' +\
        '  \nGitHub: [' + f + '](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/magazine/'+uid +'#figure-'+f.split('_')[0][3:]+')'+\
        ''+\
        '  \n\n### Light theme  \n\nVersions with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local.png) [`svg`](visualisation/' + f + local_suffix +'.svg) [`json`](visualisation/' + f + local_suffix +'.json) '+ \
        ''+\
        '  \n\n### Dark theme  \n\nVersions with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local_dark.png) [`svg`](visualisation/' + f + local_suffix +'_dark.svg) [`json`](visualisation/' + f + local_suffix+ '_dark.json) '+ \
        ''+\
        '  \n\n!["' + f + '"](visualisation/' + f + '.svg "' + f + '")\n\n' +\
        '  \n\n!["' + f + '_dark"](visualisation/' + f + '_dark.svg "' + f + '")\n\n' 
    return readme, f, fc

In [11]:
def area(base,color,base_color='#ffffff00',opacity=1,kind='area'):
    if kind=='area':
        return base.mark_area(opacity=opacity,
        interpolate="monotone",
        line={'color':color},
        color=alt.Gradient(
            gradient='linear',
            stops=[alt.GradientStop(color=base_color, offset=0.2),
                   alt.GradientStop(color=color, offset=0.8)],
            x1=1, #0.8
            y1=1,
            x2=1,
            y2=0
            )
        )
    elif kind=='line':
        return base.mark_line(opacity=opacity,interpolate="monotone",color=color)
    elif kind=='dashed-line':
        return base.mark_line(opacity=opacity,interpolate="monotone",color=color,strokeDash=[5,5])
    else:
        print('Please specify kind...')
        return

In [87]:
# service_color='#d6c8da' '#e4bfe2' '#ce4b96' colors['eco-turquiose']
service_color='#b4c8d8'

def dark(f):
    # service_color='#d6c8da' '#e4bfe2' '#ce4b96' colors['eco-turquiose']
    service_color='#b4c8d8'
    configSource = "visualisation/" + f + ".json"
    config = json.loads(open(configSource, "r").read())
    config['background']=colors['eco-background']
    def dark_layer(config):
        def dark_color(color):
            return color\
                .replace(colors['eco-gray'],service_color)\
                .replace(colors['eco-blue'],colors['eco-yellow'])\
                .replace(colors['eco-dark-blue'],colors['eco-light-blue'])\
                .replace(colors['eco-purple'],'#FF69B4')\
                .replace('#eeeeee','#224183')\
                .replace('#cccddd','#1c376f')

        for i in config['layer']:
            if 'encoding' in i:
                for x in ['x','y','color']:
                    if x in i['encoding']:
                        if 'axis' in i['encoding'][x]:
                            for c in ['domainColor','labelColor','tickColor','titleColor','gridColor']:
                                if 'axis' in i['encoding'][x]:
                                    if i['encoding'][x]['axis']!=None:
                                        if c in i['encoding'][x]['axis']:
                                            i['encoding'][x]['axis'][c]=service_color
                        if 'scale' in i['encoding'][x]:
                            if 'range' in i['encoding'][x]['scale']:
                                i['encoding'][x]['scale']['range']=[dark_color(r) for r in i['encoding'][x]['scale']['range']]
                        if 'legend' in i['encoding'][x]:
                            if i['encoding'][x]['legend']!=None:
                                if 'labelColor' in i['encoding'][x]['legend']:
                                    i['encoding'][x]['legend']['labelColor']=dark_color(i['encoding'][x]['legend']['labelColor'])
                            
            if 'mark' in i:
                if 'color' in i['mark']:
                    # manual dark_color overrides for marks only
                    if i['mark']['color']==service_color:
                        i['mark']['color']=colors['eco-green']
                    elif 'stops' in i['mark']['color']:
                        for s in i['mark']['color']['stops']:
                            if 'color' in s:
                                s['color']=dark_color(s['color'])
                    else:
                        i['mark']['color']=dark_color(i['mark']['color'])
                if 'line' in i['mark']:
                    if type(i['mark'])==str:
                        if 'color' in i['encoding']:
                            if 'scale' in i['encoding']['color']:
                                if 'range' in i['encoding']['color']['scale']:
                                    for color in i['encoding']['color']['scale']['range']:
                                        color=dark_color(color)
                    else:
                        if 'color' in i['mark']['line']:
                            i['mark']['line']['color']=dark_color(i['mark']['line']['color'])
                if 'fill' in i['mark']:
                    i['mark']['fill']=dark_color(i['mark']['fill'])
                if 'stroke' in i['mark']:
                    i['mark']['stroke']=dark_color(i['mark']['stroke'])
                    
        if 'title' in config:
            if 'color' in config['title']:
                    config['title']['color']=dark_color(config['title']['color'])
            if 'subtitle' in config['title']:
                if 'subtitleColor' in config['title']:
                    config['title']['subtitleColor']=dark_color(config['title']['subtitleColor'])
                    
        return config

    if 'vconcat' in config:
        for layer in config['vconcat']:
            layer=dark_layer(layer)
    elif 'hconcat' in config:
        for layer in config['hconcat']:
            layer=dark_layer(layer)
    else:
        config=dark_layer(config)
    
    if 'datasets' in config:
        for i in config['datasets']:
            if len(config['datasets'][i])>0:
                if 'img' in config['datasets'][i][0]:
                    if 'eco-icon-dark' in config['datasets'][i][0]['img']:
                        config['datasets'][i][0]['img']=config['datasets'][i][0]['img'].replace('eco-icon-dark','eco-icon-light')
                    if 'shipping-dark' in config['datasets'][i][0]['img']:
                        config['datasets'][i][0]['img']=config['datasets'][i][0]['img'].replace('shipping-dark','shipping-light')
    
    return alt.Chart.from_dict(config) 

- Global population (300-year trend) – "hockey-stick" line chart
- GDP per capita by major country (maybe G7 + China, India, Brazil), 300 years
- Life expectancy by continent(?) over time, 300 years if possible
- CO2 emissions (including historical), either gross or per capita (we want to show that UK/US are bad historically, but China are bad now), as far back as we can
- Processing power – Moore's law (last 60-70 years is fine)
- Trade – maybe 2x maps of main trade routes (300 years ago vs now)

# Article 1
History in numbers

## Fig 1

https://data.london.gov.uk/dataset/global-city-population-estimates  
Uni Gorningen Maddison pop dataset (2014)
https://www.rug.nl/ggdc/  
https://www.rug.nl/ggdc/historicaldevelopment/maddison/releases/maddison-project-database-2020  
https://clio-infra.eu/Indicators/TotalPopulation.html#

https://docs.google.com/spreadsheets/d/14_suWY8fCPEXV0MH7ZQMZ-KndzMVsSsA5HdR-7WqAC0/edit#gid=501532268
Gapminder v6 1800-2100

https://en.wikipedia.org/wiki/Estimates_of_historical_world_population  
https://population.un.org/wpp/Graphs/DemographicProfiles/Line/900

In [13]:
# !pip install lxml

In [14]:
dw=pd.read_html('https://en.wikipedia.org/wiki/Estimates_of_historical_world_population')[3]
dw=dw.set_index('Year').iloc[:-1].stack().reset_index()
dw.columns=['region','year','pop']
dw['pop']=dw['pop'].str.split('(').str[0].str.replace(',','').str.strip().astype(float)*1000
dw['year']=dw['year'].astype(int)

In [15]:
df1=pd.read_excel('raw/WPP2022_GEN_F01_DEMOGRAPHIC_INDICATORS_COMPACT_REV1.xlsx',skiprows=16,usecols='C,K,L',sheet_name='Estimates')
df1=df1[df1['Region, subregion, country or area *'].isin(['WORLD','OCEANIA','NORTHERN AMERICA','LATIN AMERICA AND THE CARIBBEAN',
                                                   'ASIA','EUROPE','Central Asia','Eastern Asia','Western Asia',
                                                    'South-Eastern Asia','Southern Asia','AFRICA'])]
df1.columns=['region','year','pop']
df1['year']=df1['year'].astype(int)

In [16]:
df2=pd.read_excel('raw/WPP2022_GEN_F01_DEMOGRAPHIC_INDICATORS_COMPACT_REV1.xlsx',skiprows=16,usecols='C,K,L',sheet_name='Medium variant')
df2=df2[df2['Region, subregion, country or area *'].isin(['WORLD','OCEANIA','NORTHERN AMERICA','LATIN AMERICA AND THE CARIBBEAN',
                                                   'ASIA','EUROPE','Central Asia','Eastern Asia','Western Asia',
                                                    'South-Eastern Asia','Southern Asia','AFRICA'])]
df2.columns=['region','year','pop']
df2['year']=df2['year'].astype(int)

In [17]:
df=pd.concat([dw[dw['year']<2030],df2[df2['year']>2022]]).set_index(['year','region']).unstack()['pop']

df['Africa']=df['Africa'].fillna(df['AFRICA'])
df['Asia']=df['Asia'].fillna(df['ASIA'])
df['Europe and Central Asia']=df['Europe[31]'].fillna(df['EUROPE']+df['Central Asia'])
df['East and Southeast Asia']=df['East/Southeast Asia'].fillna(df['Eastern Asia']+df['South-Eastern Asia'])
df['South Asia']=df['South Asia'].fillna(df['Southern Asia'])
df['West Asia']=df['West Asia'].fillna(df['Western Asia'])
df['World']=df['World'].fillna(df['WORLD'])
df['North America']=df['North America'].fillna(df['NORTHERN AMERICA'])
df['Latin America']=df['South/Central America'].fillna(df['LATIN AMERICA AND THE CARIBBEAN'])

df=df[['Africa','Asia','Europe and Central Asia',
    'East and Southeast Asia','South Asia','West Asia',
    'World','North America','Latin America']].T

In [18]:
dfs=df.loc[['North America', 'West Asia', 'Latin America',
       'Europe and Central Asia', 'East and Southeast Asia', 'South Asia',
       'Africa']].cumsum()
dfs/=1000000.0
dfs=dfs.T.reset_index()
dfs['stack']=True

df/=1000000.0
df=df.T.reset_index()
df['stack']=False

df=pd.concat([df,dfs])

In [19]:
readme, f, fc = save(df,"fig1-1_pop",LOCAL)

In [20]:
xmin=1700
xmax=2023
ymin=0
ymax=11
xaxis = alt.Chart(pd.DataFrame([{'x':xmin,'y':0},{'x':xmax,'y':0}])).mark_line(color=colors["eco-gray"],opacity=mo-0.2,strokeWidth=1).encode(
    x=alt.X(
        "x:Q",
        # sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
            format='.0f'
        ),
    ),
    y=alt.Y(
        "y:Q",
        sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="Population (in billions, stacked)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='.0f',
            tickCount=8
        ),
        scale=alt.Scale(domain=[ymin, ymax]),
    )
)

base = alt.Chart(fc).transform_filter('datum.stack').transform_filter('datum.year>1699')
line0=area(base,colors['eco-gray'],kind='line').encode(x='year:Q',y='Africa:Q')
line1=area(base,colors['eco-dot']).encode(x='year:Q',y2='South Asia:Q',y='Africa:Q')
line2=area(base,colors['eco-yellow']).encode(x='year:Q',y2='East and Southeast Asia:Q',y='South Asia:Q')
line3=area(base,colors['eco-turquiose']).encode(x='year:Q',y2='Europe and Central Asia:Q',y='East and Southeast Asia:Q')
line4=area(base,colors['eco-mid-blue']).encode(x='year:Q',y2='Latin America:Q',y='Europe and Central Asia:Q')
line5=area(base,colors['eco-orange']).encode(x='year:Q',y2='West Asia:Q',y='Latin America:Q')
line6=area(base,colors['eco-green']).encode(x='year:Q',y2='North America:Q',y='West Asia:Q')
line7=area(base,colors['eco-dark-blue']).encode(x='year:Q',y='North America:Q')

label0=line0.mark_text(text='World Total',color=colors['eco-gray'], align='left',dx=5,dy=5).transform_filter('datum.year==2100')
label1=line1.mark_text(text='Africa',color=colors['eco-dot'], align='left',dx=5,dy=40).transform_filter('datum.year==2100')
label2=line2.mark_text(text='South Asia',color=colors['eco-yellow'], align='left',dx=5,dy=20).transform_filter('datum.year==2100')
label3=line3.mark_text(text='East and Southeast Asia',color=colors['eco-turquiose'], align='left',dx=5,dy=10).transform_filter('datum.year==2100')
label4=line4.mark_text(text='Europe and Central Asia',color=colors['eco-mid-blue'], align='left',dx=5,dy=10).transform_filter('datum.year==2100')
label5=line5.mark_text(text='Latin America',color=colors['eco-orange'], align='left',dx=5,dy=5).transform_filter('datum.year==2100')
label6=line6.mark_text(text='West Asia',color=colors['eco-green'], align='left',dx=5,dy=5).transform_filter('datum.year==2100')
label7=line7.mark_text(text='North America',color=colors['eco-dark-blue'], align='left',dx=5,dy=5).transform_filter('datum.year==2100')

basei=alt.Chart(fc).transform_filter('!datum.stack').transform_filter('datum.year==2023')
label0i=basei.mark_text(color=colors['eco-gray'], align='right',dx=-5,dy=-90).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["World"],".2f")')
label1i=basei.mark_text(color=colors['eco-dot'], align='right',dx=-5,dy=-75).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Africa"],".2f")')
label2i=basei.mark_text(color=colors['eco-yellow'], align='right',dx=-5,dy=-30).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["South Asia"],".2f")')
label3i=basei.mark_text(color=colors['eco-turquiose'], align='right',dx=-5,dy=25).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["East and Southeast Asia"],".2f")')
label4i=basei.mark_text(color=colors['eco-mid-blue'], align='right',dx=-5,dy=85).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Europe and Central Asia"],".2f")')
label5i=basei.mark_text(color=colors['eco-orange'], align='right',dx=-5,dy=110).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Latin America"],".2f")')
label6i=basei.mark_text(color=colors['eco-green'], align='right',dx=-5,dy=123).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["West Asia"],".2f")')
label7i=basei.mark_text(color=colors['eco-dark-blue'], align='right',dx=-5,dy=135).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["North America"],".2f")')

basei=alt.Chart(fc).transform_filter('!datum.stack').transform_filter('datum.year==2100')
label0p=basei.mark_text(color=colors['eco-gray'], align='right',dx=-5,dy=190).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["World"],".2f")')
label1p=basei.mark_text(color=colors['eco-dot'], align='right',dx=-5,dy=-140).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Africa"],".2f")')
label2p=basei.mark_text(color=colors['eco-yellow'], align='right',dx=-5,dy=120).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["South Asia"],".2f")')
label3p=basei.mark_text(color=colors['eco-turquiose'], align='right',dx=-5,dy=25).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["East and Southeast Asia"],".2f")')
label4p=basei.mark_text(color=colors['eco-mid-blue'], align='right',dx=-5,dy=77).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Europe and Central Asia"],".2f")')
label5p=basei.mark_text(color=colors['eco-orange'], align='right',dx=-5,dy=100).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["Latin America"],".2f")')
label6p=basei.mark_text(color=colors['eco-green'], align='right',dx=-5,dy=118).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["West Asia"],".2f")')
label7p=basei.mark_text(color=colors['eco-dark-blue'], align='right',dx=-5,dy=133).encode(text='t:Q',x='year:Q').transform_calculate(t='format(datum["North America"],".2f")')

area2l=alt.Chart(pd.DataFrame([{'x':2023,'y':0,'y2':11.5},{'x':2100,'y':0,'y2':11.5}])).mark_line(opacity=0.5,strokeDash=[5,5],strokeWidth=1).encode(x='x:Q',y='y:Q',y2='y2:Q')
label2l=alt.Chart(pd.DataFrame([{'x':2023,'y':11}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='2023',align='right',
                                                               dx=-5,dy=-5,baseline='bottom').encode(x='x:Q',y='y:Q')
label2p=alt.Chart(pd.DataFrame([{'x':2100,'y':11}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='2100',align='right',
                                                               dx=-5,dy=-5,baseline='bottom').encode(x='x:Q',y='y:Q')
label2r=alt.Chart(pd.DataFrame([{'x':2100,'y':11}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='projection',align='left',
                                                               dx=5,dy=-5,baseline='bottom').encode(x='x:Q',y='y:Q')
area2e=alt.Chart(pd.DataFrame([{'x':2023,'y':8,'y2':11.5},{'x':2070,'y':8,'y2':11.5}])).mark_area(
    opacity=0.4,
    color=alt.Gradient(
        gradient='linear',
        stops=[alt.GradientStop(color='#ffffff00', offset=0),
               alt.GradientStop(color=colors["eco-gray"], offset=1)],
        x1=1,
        y1=1,
        x2=0,
        y2=1
        )
    ).encode(x='x:Q',y='y:Q',y2='y2:Q')

layer1l=(xaxis+area2e+line1+line2+line3+line4+line5+line6+line7+line0+area2l+label2l+label2p+label2r+\
        label1+label2+label3+label4+label5+label6+label7+label0).properties(height=300, width=300, 
        title={'text':"In the past 300 years global population grew ten-fold",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Gapminder (v6) based on UN Population Division & Angus Maddison/CLIO, 2019','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})

xaxis = xaxis.encode(
    x=alt.X(
        "x:N",
        # sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0
        ),
    ),
    y=alt.Y(
        "y:Q",
        sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='.1f',
            tickCount=8
        )
    )
)
base = alt.Chart(fc).transform_filter('!datum.stack').transform_filter('(datum.year==1700) | (datum.year==2023) | (datum.year==2100)')
line1=base.mark_line(color=colors['eco-dot'],opacity=0.7).encode(x='year:N',y='Africa:Q')
point1=base.mark_circle(color=colors['eco-dot'],opacity=0.7).encode(x='year:N',y='Africa:Q')

base=base.transform_fold(
    ['North America', 'West Asia', 'Latin America',
       'Europe and Central Asia', 'East and Southeast Asia', 'South Asia',
       'Africa']
).transform_joinaggregate(
     min='min(value)',
     max='max(value)',
     groupby=['year']
).transform_calculate(
    minmax_value=(datum.value-datum.min)/(datum.max-datum.min),
    mid=(datum.min+datum.max)/2
).transform_calculate(xmax='format(datum.max,".2f")'
).transform_calculate(xmid='format(datum.mid,".2f")'
).transform_calculate(xmin='format(datum.min,".2f")'
).properties(height=300, width=200, title="")
lines = base.mark_line(opacity=0.8).encode(
    x=alt.X('year:N',axis=alt.Axis(grid=False,
    title="",
    labelColor=colors["eco-gray"],
    titleColor=colors["eco-gray"],
    tickColor=colors["eco-gray"],
    tickCount=3,
    domain=False,
    tickOpacity=mo,
    labelOpacity=mo+0.2,
    titleOpacity=mo+0.3,
    titleFontSize=12,
    orient="bottom",
    labelAngle=0)),
    y=alt.Y('minmax_value:Q',axis=alt.Axis(grid=False,
    gridDash=[1,5],
    gridColor=colors["eco-gray"],
    gridOpacity=mo,
    title="",
    ticks=False,
    labels=False,
    domain=False,
    tickCount=8)),
    color=alt.Color('key:N',legend=None,scale=alt.Scale(
        range=[colors['eco-dot'],colors['eco-turquiose'],colors['eco-mid-blue'],colors['eco-orange'],colors['eco-dark-blue'],colors['eco-yellow'],colors['eco-green']]
    )),
    detail='key:N'
)
points=lines.mark_circle(opacity=1)
labels=lines.mark_text(align='left',dx=5).encode(text='key:N').transform_filter('datum.year==2100')
labels1=labels.transform_filter('(datum.key!="North America") & (datum.key!="Europe and Central Asia")')
labels2=labels.mark_text(align='left',dx=20,dy=12).transform_filter('datum.key=="North America"')
labels3=labels.mark_text(align='left',dx=5,dy=-12).transform_filter('datum.key=="Europe and Central Asia"')

rule1 = base.mark_rule(
    color=colors['eco-gray'], opacity=0.1
).encode(
    x="year:N",
    detail="key:Q",
).transform_filter('datum.year!=2100')
rule2 = base.mark_rule(strokeDash=[5,5],
    color=colors['eco-gray'], opacity=0.1
).encode(
    x="year:N",
    detail="key:Q",
).transform_filter('datum.year==2100')

def ytick(yvalue, field):
    scale = base.encode(x='year:N', y=alt.value(yvalue), text=f"{field}:Q")
    return alt.layer(
        scale.mark_text(baseline="middle", align="right", dx=-4, dy=-6, opacity=0.1,color=colors['eco-gray']),
        scale.mark_tick(size=24, opacity=0.1,color=colors['eco-gray'], orient="horizontal",xOffset=-12)
    )

layer1r=alt.layer(
    lines, points, rule1, rule2, ytick(0, "xmax"), ytick(150, "xmid"), ytick(300, "xmin"), labels1, labels2, labels3
).properties(
        title={'text':"Global regions ranked by population",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':20,'fontSize':15
              })

layer1=alt.hconcat(layer1l,layer1r).configure(font='Circular Std Book').configure_view(stroke=None)

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "w").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()

# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-1_pop



alt.HConcatChart(...)

alt.HConcatChart(...)

## Fig 2

In [1099]:
df=pd.read_csv('raw/life-expectancy.csv')
df=df[df['Entity'].isin(['Africa', 'Americas', 'Asia', 'Europe',
       'Sweden', 'United Kingdom', 'World','Canada','Japan','Russia','United States','India','Australia','Argentina','Oceania'])].drop('Code',axis=1)
df.columns=['key','year','value']

In [1100]:
readme, f, fc = save(df,"fig1-2_life_expectancy",LOCAL)

In [1107]:
base=alt.Chart(fc)
lines = base.mark_line(opacity=0.8,clip=True,interpolate='monotone').encode(
    x=alt.X('year:Q',axis=alt.Axis(
            grid=True,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            titleAlign="left",
            titleAnchor="end",
            title="",
        titleX=405,
            titleY=6,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=10,
            titleFontWeight='normal',
            orient="bottom",
            format='.0f',
            labelAngle=0
            ),
            scale=alt.Scale(domain=[1700,2021],nice=False)
    ),
    y=alt.Y('value:Q',axis=alt.Axis( 
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="Lie expectancy at birth (years)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='s',
            tickCount=8,
            # domain=False,
            # labels=False
        ),
            scale=alt.Scale(domain=[10,90])
    
           ),
    color=alt.Color('key:N',legend=None,scale=alt.Scale(
        range=[colors['eco-mid-blue'],colors['eco-purple'],colors['eco-mid-blue'],colors['eco-mid-blue'],
               colors['eco-dark-blue'],colors['eco-dark-blue'],
            colors['eco-turquiose'],colors['eco-turquiose'],colors['eco-turquiose'],
               colors['eco-yellow'],colors['eco-yellow'],
               colors['eco-green'],colors['eco-green'],colors['eco-green'],
               colors["eco-gray"],colors["eco-gray"],
               colors["eco-orange"],colors["eco-orange"],
               colors['eco-dot'],colors['eco-dot'],colors['eco-dot'],colors['eco-dot']
               ],
        domain=["Russia",'United Kingdom','France','Germany',
                'United States','Canada',
                'Japan','China','Asia',
                'India','Pakistan',
                'Turkey','Saudi Arabia','United Arab Emirates',
                'Australia','World',
                'Americas','Argentina',
                'Egypt','Nigeria','South Africa','Africa']
    ))
)
uk=lines.mark_line(opacity=0.8,clip=True,interpolate='monotone',color=colors['eco-purple'],strokeWidth=3).transform_filter('datum.key=="United Kingdom"')

labels=lines.mark_text(align='left',dx=5).encode(text='t:N').transform_filter('datum.year==2021').transform_calculate(t='datum.key'
)
labels1=labels.transform_filter({'not': alt.FieldOneOfPredicate(oneOf=['Australia','Canada','Japan','Americas','Argentina','Asia','World'],field="key")})
labels2=labels.mark_text(align='left',dx=5,dy=-7).transform_filter('datum.key=="Australia"')
labels3=labels.mark_text(align='left',dx=5,dy=-3).transform_filter('datum.key=="Canada"')
labels4=labels.mark_text(align='left',dx=5,dy=-17).transform_filter('datum.key=="Japan"')
labels5=labels.mark_text(align='left',dx=5,dy=3).transform_filter('datum.key=="Argentina"')
labels6=labels.mark_text(align='left',dx=5,dy=2).transform_filter('datum.key=="Asia"')
labels7=labels.mark_text(align='left',dx=-312,dy=157).transform_filter('datum.key=="Americas"')
labels8=labels.mark_text(align='left',dx=-230,dy=150).transform_filter('datum.key=="World"')

layer1=(lines+uk+labels1+labels2+labels3+labels4+labels5+labels6+labels7+labels8
       ).\
    configure(font='Circular Std Book').configure_view(stroke=None,discreteWidth=400,discreteHeight=300,continuousWidth=400,continuousHeight=300).properties( 
        title={'text':"In the past 300 years life expectancy has doubled",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Riley, 2005; Zijdeman et al./CLIO, 2015; UN WPP, 2022','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-2_life_expectancy



alt.LayerChart(...)

alt.LayerChart(...)

## Fig 3

https://www.gapminder.org/data/documentation/gd001/

In [1108]:
df=pd.read_excel('raw/gapdata001 v11.xlsx',sheet_name='Data & metadata',usecols='A,B,D')
df=df[df['Year'].isin([1700,1750])].dropna().set_index(['Area','Year']).unstack()['GDP per capita - with interpolations']
df=df[~df.index.isin(['USSR','Czechoslovakia','Yugoslavia','Eritrea and Ethiopia'])]

In [1109]:
df2=pd.read_excel('raw/GM-GDP per capita - Dataset - v28.xlsx',sheet_name='data-for-countries-etc-by-year',usecols='B:D')
df2=df2[df2['time'].isin([1800,1850,1900,1950,2000,2023,2050])].dropna().set_index(['name','time']).unstack()['Income per person']

In [1110]:
df=df2.join(df).dropna(subset=[2023])
df=df.stack().reset_index()
df.columns=['key','year','value']

In [1111]:
readme, f, fc = save(df,"fig1-3_gdp",LOCAL)

In [1115]:
base=alt.Chart(fc).transform_filter(alt.FieldOneOfPredicate(oneOf=["Russia",'United Kingdom','United States',
        'Japan','Germany','India','China','Egypt','Pakistan','Turkey',
        'Nigeria','South Africa','United Arab Emirates'],field="key"))
lines = base.mark_line(opacity=0.8,clip=True,interpolate='monotone').encode(
    x=alt.X('year:Q',axis=alt.Axis(
            grid=True,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            titleAlign="left",
            titleAnchor="end",
            title="(projection)",
        titleX=405,
            titleY=6,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=10,
            titleFontWeight='normal',
            orient="bottom",
            format='.0f',
            labelAngle=0,
            # scale=alt.Scale(domain=[1700,2100])
    )),
    y=alt.Y('value:Q',axis=alt.Axis( 
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="GDP per capita, adjusted for PPP, in constant 2017 international USD (log scale)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='s',
            tickCount=8,
            # domain=False,
            # labels=False
        ),
            scale=alt.Scale(type='log',domain=[400,200000])
    
           ),
    color=alt.Color('key:N',legend=None,scale=alt.Scale(
        range=[colors['eco-mid-blue'],colors['eco-purple'],colors['eco-mid-blue'],colors['eco-mid-blue'],
               colors['eco-dark-blue'],colors['eco-dark-blue'],
            colors['eco-turquiose'],colors['eco-turquiose'],
               colors['eco-yellow'],colors['eco-yellow'],
               colors['eco-green'],colors['eco-green'],colors['eco-green'],
               colors["eco-gray"],
               colors['eco-dot'],colors['eco-dot'],colors['eco-dot']
               ],
        domain=["Russia",'United Kingdom','France','Germany',
                'United States','Canada',
        'Japan','China',
                'India','Pakistan',
                'Turkey','Saudi Arabia','United Arab Emirates',
                'Australia',
                'Egypt','Nigeria','South Africa']
    ))
)
uk=lines.mark_line(opacity=0.8,clip=True,interpolate='monotone',color=colors['eco-purple'],strokeWidth=3).transform_filter('datum.key=="United Kingdom"')

labels=lines.mark_text(align='left',dx=5).encode(text='t:N').transform_filter('datum.year==2050').transform_calculate(t='datum.key'
)
labels1=labels.transform_filter({'not': alt.FieldOneOfPredicate(oneOf=['Pakistan','India','Russia',
                        'United Kingdom','United Arab Emirates'],field="key")})
labels2=labels.mark_text(align='left',dx=5,dy=-5).transform_filter('datum.key=="Pakistan"')
labels3=labels.mark_text(align='left',dx=5,dy=5).transform_filter('datum.key=="India"')
labels4=labels.mark_text(align='left',dx=5,dy=7).transform_filter('datum.key=="Russia"')
labels5=labels.mark_text(align='left',dx=5,dy=-7).transform_filter('datum.key=="United Arab Emirates"')
labels6=labels.mark_text(align='left',dx=55).transform_filter('datum.key=="United Kingdom"')

area2l=alt.Chart(pd.DataFrame([{'x':2023,'y':400,'y2':200000},{'x':2050,'y':400,'y2':200000}])).mark_line(opacity=0.5,strokeDash=[5,5],strokeWidth=1
                                                                                                         ).encode(x=alt.X('x:Q',
                ),y=alt.Y('y:Q',scale=alt.Scale(type='log',domain=[400,200000])),y2='y2:Q')
label2l=alt.Chart(pd.DataFrame([{'x':2023,'y':200000}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='2023',align='right',
                                                               dx=-5,dy=5,baseline='top').encode(x=alt.X('x:Q',
                ),y=alt.Y('y:Q',scale=alt.Scale(type='log',domain=[400,200000])),y2='y2:Q')
label2p=alt.Chart(pd.DataFrame([{'x':2050,'y':11}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='2100',align='right',
                                                               dx=-5,dy=-5,baseline='bottom').encode(x='x:Q',y='y:Q')
label2r=alt.Chart(pd.DataFrame([{'x':2050,'y':11}])).mark_text(opacity=0.5,color=colors['eco-gray'],text='projection',align='left',
                                                               dx=5,dy=-5,baseline='bottom').encode(x='x:Q',y='y:Q')
area2e=alt.Chart(pd.DataFrame([{'x':2023,'y':400,'y2':200000},{'x':2050,'y':400,'y2':200000}])).mark_area(
    opacity=0.4,
    color=alt.Gradient(
        gradient='linear',
        stops=[alt.GradientStop(color='#ffffff00', offset=0),
               alt.GradientStop(color=colors["eco-gray"], offset=1)],
        x1=1,
        y1=1,
        x2=0,
        y2=1
        )
    ).encode(x=alt.X('x:Q',
                ),y=alt.Y('y:Q',scale=alt.Scale(type='log',domain=[400,200000])),y2='y2:Q')

points=lines.mark_circle(opacity=1).transform_filter('datum.year==2023')
layer1=(lines+uk+area2e+label2l+points+labels1+labels2+labels3+labels4+labels5+labels6).\
    configure(font='Circular Std Book').configure_view(stroke=None,discreteWidth=400,discreteHeight=300,continuousWidth=400,continuousHeight=300).properties( 
        title={'text':"In the past 300 years global GDP per capita grew twenty-fold",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Gapminder (v28) based on World Bank World Development Indicators & Angus Maddison/CLIO, 2022','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})

if SAVE:
    layer1.save("visualisation/" + f + "_no_branding.json")
    layer1.save("visualisation/" + f + "_no_branding.svg")
    layer1.save("visualisation/" + f + "_no_branding.png")
    layer2=dark(f+'_no_branding')
    layer2.save("visualisation/" + f + "_no_branding_dark.json")
    layer2.save("visualisation/" + f + "_no_branding_dark.svg")
    layer2.save("visualisation/" + f + "_no_branding_dark.png")

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-3_gdp



alt.LayerChart(...)

alt.LayerChart(...)

## Fig 4

In [1116]:
df=pd.read_csv('raw/annual-co-emissions-by-region.csv')
df=df[df['Entity'].isin(['Africa', 'China','India','United States',
       'Asia (excl. China and India)', 'Europe (excl. EU-27)', 'United Kingdom',
       'European Union (27)',
       'International transport', 
       'North America (excl. USA)', 'Oceania',
       'South America'])].drop('Code',axis=1)
df.columns=['key','year','value']

In [1117]:
df=df.set_index(['year','key']).unstack()['value']
df['Europe (excl. EU-27)']-=df['United Kingdom']
df1=(df[['United Kingdom', 'Oceania', 'International transport', 'South America',
       'North America (excl. USA)', 'Africa', 'Europe (excl. EU-27)', 'India',
       'European Union (27)', 'United States', 'Asia (excl. China and India)',
       'China']]/1000000000.0).rename(columns={'Europe (excl. EU-27)':'Europe (excl. EU-27 and UK)'})
df2=df1.T.cumsum().T
df1['stack']=False
df2['stack']=True
df=pd.concat([df1,df2]).reset_index()

In [1118]:
readme, f, fc = save(df,"fig1-4_emissions",LOCAL)

In [1125]:
xmin=1700
xmax=2021
ymin=0
ymax=40
xaxis = alt.Chart(pd.DataFrame([{'x':xmin,'y':0},{'x':xmax,'y':0}])).mark_line(color=colors["eco-gray"],opacity=mo-0.2,strokeWidth=1).encode(
    x=alt.X(
        "x:Q",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
            format='.0f'
        ),
        scale=alt.Scale(domain=[xmin, xmax],nice=False),
    ),
    y=alt.Y(
        "y:Q",
        sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="Emissions (billion tonnes, CO₂ equivalent)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='.0f',
            tickCount=8
        ),
        scale=alt.Scale(domain=[ymin, ymax]),
    )
)

base = alt.Chart(fc).transform_filter('datum.stack').transform_filter('datum.year>1749')\
    .transform_calculate(lz1='datum["Asia (excl. China and India)"]')\
    .transform_calculate(lz2='datum["European Union (27)"]')\
    .transform_calculate(lz5='datum["Europe (excl. EU-27 and UK)"]')\
    .transform_calculate(lz7='datum["North America (excl. USA)"]')
line0=area(base,colors['eco-gray'],kind='line').encode(x='year:Q',y='China:Q')
line1=area(base,colors['eco-turquiose']).encode(x='year:Q',y2='lz1:Q',y='China:Q')
line2=area(base,'#135d4f').encode(x='year:Q',y2='United States:Q',y='lz1:Q')
line3=area(base,colors['eco-dark-blue']).encode(x='year:Q',y2='lz2:Q',y='United States:Q')
line4=area(base,colors['eco-mid-blue']).encode(x='year:Q',y2='India:Q',y='lz2:Q')
line5=area(base,colors['eco-yellow']).encode(x='year:Q',y2='lz5:Q',y='India:Q')
line6=area(base,colors['eco-mid-blue']).encode(x='year:Q',y2='Africa:Q',y='lz5:Q')
line7=area(base,colors['eco-dot']).encode(x='year:Q',y2='lz7:Q',y='Africa:Q')
line8=area(base,colors['eco-dark-blue']).encode(x='year:Q',y2='South America:Q',y='lz7:Q')
line9=area(base,colors['eco-orange']).encode(x='year:Q',y2='International transport:Q',y='South America:Q')
line10=area(base,colors['eco-gray']).encode(x='year:Q',y2='Oceania:Q',y='International transport:Q')
line11=area(base,colors['eco-gray']).encode(x='year:Q',y2='United Kingdom:Q',y='Oceania:Q')
line12=area(base,colors['eco-purple']).encode(x='year:Q',y='United Kingdom:Q')

label0=line0.mark_text(text='World Total',
                       color=line0.to_dict()['mark']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label1=line1.mark_text(text='China',
                       color=line1.to_dict()['mark']['line']['color'], align='left',dx=5,dy=40).transform_filter('datum.year==2021')
label2=line2.mark_text(text='Asia (excl. China and India)',
                       color=line2.to_dict()['mark']['line']['color'], align='left',dx=5,dy=20).transform_filter('datum.year==2021')
label3=line3.mark_text(text='United States',
                       color=line3.to_dict()['mark']['line']['color'], align='left',dx=5,dy=10).transform_filter('datum.year==2021')
label4=line4.mark_text(text='EU-27',
                       color=line4.to_dict()['mark']['line']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label5=line5.mark_text(text='India',
                       color=line5.to_dict()['mark']['line']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label6=line6.mark_text(text='Europe (excl. EU-27 and UK)',
                       color=line6.to_dict()['mark']['line']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label7=line7.mark_text(text='Africa',
                       color=line7.to_dict()['mark']['line']['color'], align='left',dx=5,dy=2).transform_filter('datum.year==2021')
label8=line8.mark_text(text='North America (excl. USA)',
                       color=line8.to_dict()['mark']['line']['color'], align='left',dx=5,dy=3).transform_filter('datum.year==2021')
label9=line9.mark_text(text='South America',
                       color=line9.to_dict()['mark']['line']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label10=line10.mark_text(text='International transport',
                       color=line10.to_dict()['mark']['line']['color'], align='left',dx=5,dy=8).transform_filter('datum.year==2021')
label11=line11.mark_text(text='Oceania',
                       color=line11.to_dict()['mark']['line']['color'], align='left',dx=5,dy=5).transform_filter('datum.year==2021')
label12=line12.mark_text(text='United Kingdom',
                       color=line12.to_dict()['mark']['line']['color'], align='left',dx=15,dy=10).transform_filter('datum.year==2021')

layer1l=(xaxis+line1+line2+line3+line4+line5+line6+line7+line8+line9+line10+line11+line12+line0+\
        label1+label2+label3+label4+label5+label6+label7+label8+label9+label10+label12+label0
        ).properties(height=300, width=300, 
        title={'text':"In the past 300 years global emissions grew to 40 billion tonnes",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Global Carbon Project, 2023','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})

xaxis = xaxis.encode(
    x=alt.X(
        "x:N",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0
        )
    ),
    y=alt.Y(
        "y:Q",
        sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='.1f',
            tickCount=8
        )
    )
)
base = alt.Chart(fc).transform_filter('!datum.stack')\
    .transform_filter('(datum.year==1800) | (datum.year==1900) | (datum.year==2021)')\
    .transform_calculate(lz1='datum["Asia (excl. China and India)"]')\
    .transform_calculate(lz2='datum["European Union (27)"]')\
    .transform_calculate(lz5='datum["Europe (excl. EU-27 and UK)"]')\
    .transform_calculate(lz7='datum["North America (excl. USA)"]')

base=base.transform_fold(
    ['United Kingdom', 'Oceania', 'International transport',
       'South America', 'lz7', 'Africa',
       'lz5', 'India', 'lz2',
       'United States', 'lz1', 'China']
).transform_joinaggregate(
     min='min(value)',
     max='max(value)',
     groupby=['year']
).transform_calculate(
    minmax_value=(datum.value-datum.min)/(datum.max-datum.min),
    mid=(datum.min+datum.max)/2
).transform_calculate(xmax='format(datum.max,".2f")'
).transform_calculate(xmid='format(datum.mid,".2f")'
).transform_calculate(xmin='format(datum.min,".2f")'
).transform_filter('(datum.key=="United Kingdom") | (datum.key=="China") | (datum.key=="India") | (datum.key=="United States") | (datum.key=="Africa") | (datum.key=="India") | (datum.key=="lz2")'
).properties(height=300, width=200, title="")
lines = base.mark_line(opacity=0.8).encode(
    x=alt.X('year:N',axis=alt.Axis(grid=False,
    title="",
    labelColor=colors["eco-gray"],
    titleColor=colors["eco-gray"],
    tickColor=colors["eco-gray"],
    tickCount=3,
    domain=False,
    tickOpacity=mo,
    labelOpacity=mo+0.2,
    titleOpacity=mo+0.3,
    titleFontSize=12,
    orient="bottom",
    labelAngle=0)),
    y=alt.Y('minmax_value:Q',axis=alt.Axis(grid=False,
    gridDash=[1,5],
    gridColor=colors["eco-gray"],
    gridOpacity=mo,
    title="",
    ticks=False,
    labels=False,
    domain=False,
    tickCount=8)),
    color=alt.Color('key:N',legend=None,scale=alt.Scale(
        range=[colors['eco-dot'],colors['eco-turquiose'],colors['eco-yellow'],colors['eco-purple'],colors['eco-dark-blue'],colors['eco-mid-blue'],colors['eco-green']]
    )),
    detail='key:N'
)
points=lines.mark_circle(opacity=1)
labels=lines.mark_text(align='left',dx=5).encode(text='key:N').transform_filter('datum.year==2021')
labels1=labels.transform_filter('(datum.key!="lz2")')
labels2=lines.mark_text(align='left',dx=5,dy=-15,text='EU-27').transform_filter('datum.key=="lz2"').transform_filter('datum.year==2021')

rule1 = base.mark_rule(
    color=colors['eco-gray'], opacity=0.1
).encode(
    x="year:N",
    detail="key:Q",
)

def ytick(yvalue, field):
    scale = base.encode(x='year:N', y=alt.value(yvalue), text=f"{field}:Q")
    return alt.layer(
        scale.mark_text(baseline="middle", align="right", dx=-4, dy=-6, opacity=0.1,color=colors['eco-gray']),
        scale.mark_tick(size=24, opacity=0.1,color=colors['eco-gray'], orient="horizontal",xOffset=-12)
    )

layer1r=alt.layer(
    lines, points, rule1, ytick(0, "xmax"), ytick(150, "xmid"), ytick(300, "xmin"), labels1, labels2
).properties(
        title={'text':"Global regions ranked by emissions",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':20,'fontSize':15
              })

layer1=alt.hconcat(layer1l,layer1r).configure(font='Circular Std Book').configure_view(stroke=None)

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()

# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-4_emissions



alt.HConcatChart(...)

alt.HConcatChart(...)

## Fig 5

https://en.wikipedia.org/wiki/Transistor_count

In [1126]:
df = pd.read_html("https://en.wikipedia.org/wiki/Transistor_count")[3].iloc[:-1]
df['Year']=df['Year'].str.split('[').str[0].astype(int)
df['Transistor count']=df['Transistor count'].str.split('[').str[0].str.split(' ').str[0].str.split('–').str[0].str.split('+').str[0].str.replace(',','')\
    .replace('?',np.nan).astype(float)
df=df.dropna(subset=['Transistor count'])
df=df[['Processor','Transistor count','Year','Designer']]
df['Designer']=df['Designer'].replace({
'Garrett AiResearch':'Other', 'Texas Instruments':'Other', 'NEC':'Other',
       'Toshiba':'Other', 'Motorola':'Other', 'MOS Technology':'Other', 'Intersil':'Other', 'RCA':'Other',
       'Zilog':'Other', 'Bell Labs':'Other', 'WDC':'Other', 'Acorn':'ARM', 'Harris Corporation':'Other',
       'Hitachi':'Other', 'DEC WRL':'Other', 'MIPS':'Other',  'DEC':'Other',
       'Offete Enterprises':'Other', 'Apple, IBM, Motorola':'Apple', 'Acorn, DEC, Apple':'ARM',
       'HP':'Other',  'Nordic VLSI/Atmel':'Other', 'Samsung':'Other', 'Sony, Toshiba':'Other',
       'IBM, Nintendo':'IBM', 'Sony, IBM, Toshiba':'IBM', 'Matsushita':'Other', 'Sun/Oracle':'Other',
        'Microsoft, AMD':'AMD', 'Oracle':'Other', 'Huawei':'Other',
       'Gisselquist Technology':'Other', 'SiFive':'Other', 'Nvidia':'Other', 'Amazon':'Other',
       'Mediatek':'Other'
})

In [1127]:
readme, f, fc = save(df,"fig1-5_moore",LOCAL)

In [1169]:
base=alt.Chart(fc).mark_circle(size=50,opacity=0.7).encode(
     x=alt.X('Year:Q',axis=alt.Axis(
            grid=True,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            titleAlign="left",
            titleAnchor="end",
            title="",
        titleX=505,
            titleY=6,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=10,
        titleFontWeight='normal',
            orient="bottom",
            format='.0f',
            labelAngle=0),
            scale=alt.Scale(domain=[1970,2023])
    ),
    y=alt.Y('Transistor count:Q',axis=alt.Axis( 
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="Transistor count on a single microchip (log scale)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='s',
            tickCount=8
            # domain=False,
            # labels=False
        ),
            scale=alt.Scale(type='log',domain=[400,120000000000])
    
           ),
    color=alt.Color("Designer:N",legend=alt.Legend(title='',orient='top-left',
                                                   labelOpacity=0.8,labelColor=colors['eco-gray'],labelFont='Circular Std Book'),scale=alt.Scale(
    range=[colors['eco-turquiose'],colors['eco-orange'],colors['eco-gray'],
           colors['eco-green'],colors['eco-mid-blue'],colors['eco-light-blue'],colors['eco-yellow'],colors['eco-dot']]
)))
empty=alt.Chart(pd.DataFrame([{'a':0}])).mark_text()
layer1 = (
    (base+empty)
).configure(font='Circular Std Book').configure_view(stroke=None,
                                                     discreteWidth=400,discreteHeight=300,
                                                     continuousWidth=400,continuousHeight=300).properties(
title={'text':"The number of transistors on a microchip doubles every two years",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Wikipedia/Transistor_count, 2023','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15},
)

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-5_moore



alt.LayerChart(...)

alt.LayerChart(...)

## Fig 6

In [1170]:
df=pd.read_csv('raw/annual-working-hours-per-worker.csv')
df=df[df['Entity'].isin(['Australia', 'Belgium', 'Canada', 'France', 'Germany',
       'Ireland', 'Spain', 'Sweden','Japan',
       'United Kingdom', 'United States','South Korea','Hong Kong','Chile'])].drop('Code',axis=1)
df.columns=['key','year','value']

In [1171]:
readme, f, fc = save(df,"fig1-6_hours_worked",LOCAL)

In [1179]:
base=alt.Chart(fc)
lines = base.mark_line(opacity=0.8,clip=True,interpolate='monotone').encode(
    x=alt.X('year:Q',axis=alt.Axis(
            grid=True,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            titleAlign="left",
            titleAnchor="end",
            title="",
        titleX=405,
            titleY=6,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=10,
            titleFontWeight='normal',
            orient="bottom",
            format='.0f',
            labelAngle=0
            ),
            scale=alt.Scale(domain=[1870,2019],nice=False)
    ),
    y=alt.Y('value:Q',axis=alt.Axis( 
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="Average working hours per worker over a year (hours)",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            titleFontWeight='normal',
            format='s',
            tickCount=8,
            # domain=False,
            # labels=False
        ),
            scale=alt.Scale(domain=[1000,3500])
    
           ),
    color=alt.Color('key:N',legend=None,scale=alt.Scale(
        range=[colors['eco-mid-blue'],colors['eco-purple'],"#aaa",
            colors['eco-dot'],colors['eco-dot'],colors['eco-red'],
               colors['eco-dark-blue'],colors['eco-dark-blue'],
            colors['eco-turquiose'],colors['eco-turquiose'],colors['eco-turquiose'],
               colors['eco-yellow'],colors['eco-yellow'],
               colors['eco-green'],colors['eco-yellow'],
               colors['eco-green'],colors['eco-green'],colors['eco-green'],
               colors["eco-gray"],colors["eco-gray"],
               colors["eco-orange"],colors["eco-orange"],colors["eco-orange"],
               colors['eco-dot'],colors['eco-dot'],colors['eco-dot'],colors['eco-dot']
               ],
        domain=["Belgium",'United Kingdom','Germany',
                'Ireland', 'Spain1', 'Sweden',
                'United States','Canada1',
                'France','China','Asia',
                'India','Pakistan',
                 'South Korea','Hong Kong',
                'Turkey','Saudi Arabia','United Arab Emirates',
                'Australia','World',
                'Americas','Argentina','Chile',
                'Egypt','Nigeria','South Africa','Africa']
    ))
)
uk=lines.mark_line(opacity=0.8,clip=True,interpolate='monotone',color=colors['eco-purple'],strokeWidth=3).transform_filter('datum.key=="United Kingdom"')

labels=lines.mark_text(align='left',dx=5).encode(text='t:N').transform_filter('datum.year==2017').transform_calculate(t='datum.key'
)
labels1=labels.transform_filter({'not': alt.FieldOneOfPredicate(oneOf=['Australia','Canada','Japan','Spain','Ireland',
                                                                      'Sweden','France'],field="key")})
labels2=labels.mark_text(align='left',dx=5,dy=-14).transform_filter('datum.key=="Australia"')
labels3=labels.mark_text(align='left',dx=60,dy=-11).transform_filter('datum.key=="Ireland"')
labels4=labels.mark_text(align='left',dx=5,dy=7).transform_filter('datum.key=="France"')
labels5=labels.mark_text(align='left',dx=60,dy=7).transform_filter('datum.key=="Sweden"')

layer1=(lines+uk+labels1+labels2+labels3+labels4+labels5
       ).\
    configure(font='Circular Std Book').configure_view(stroke=None,discreteWidth=400,discreteHeight=300,continuousWidth=400,continuousHeight=300).properties( 
        title={'text':"In the past 150 years working hours halved",'color':colors['eco-gray']+'dd','align':'left','anchor':'start','offset':-360,
              'subtitle':'Source: Huberman and Minns, 2007 & Penn World Tables (v9.1), 2019','subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig1-6_hours_worked



alt.LayerChart(...)

alt.LayerChart(...)

# Article 7
History of Trade

## Map 1

In [21]:
# !pip install vega_datasets

In [22]:
from vega_datasets import data
sphere = alt.sphere()
graticule = alt.graticule()
source = alt.topo_feature(data.world_110m.url, 'countries')

In [23]:
df=pd.read_csv('raw/cliwoc21.csv').dropna()
df['LAT']=pd.to_numeric((df['LAT'].str[:-2]+'.'+df['LAT'].str[-2:]), errors='coerce')
df['LON']=pd.to_numeric((df['LON'].str[:-2]+'.'+df['LON'].str[-2:]), errors='coerce')
df['time']=pd.to_datetime(df['YR'].astype(str)+'-'+df['MO'].astype(str)+'-'+df['DY'].astype(str),errors='ignore')
df['YR']=pd.to_numeric(df['YR'], errors='coerce')
df['MO']=pd.to_numeric(df['MO'], errors='coerce')
df['DY']=pd.to_numeric(df['DY'], errors='coerce')
# df=df.sort_values(by=['C1','ID','VoyageIni','YR','MO','DY','LAT','LON'])
# df['ID']=df['ID'].astype(str)+'#'+df['VoyageIni'].astype(str)
df=df.dropna(how='any')
df=df.groupby(['C1','ID','YR','MO','DY'])[['LAT','LON']].mean().reset_index()
df['index']=df.index
df=df[df['C1'].isin(['UK','NL','ES'])]
# df=df[~((df['LON']<220)&(df['LON']>160))]

/tmp/ipykernel_66/1930170559.py:1: DtypeWarning: Columns (0,1,2,3,4,5,6,8) have mixed types. Specify dtype option on import or set low_memory=False.
  df=pd.read_csv('raw/cliwoc21.csv').dropna()


In [24]:
readme, f, fc = save(df,"fig7-1_map_historical_shipping",LOCAL)

In [104]:
route_op=0.1
route_sz=0.6
background=alt.layer(
    alt.Chart(sphere).mark_geoshape(fill='#cccddd'),
    alt.Chart(source).mark_geoshape(fill='#eeeeee', stroke='#cccddd',opacity=1)
).project(
    'naturalEarth1'
).properties(title={'text':" ",'color':colors['eco-gray']+'dd','offset':-385,
              'subtitle':"Source: Climatological Database for the World's Oceans, CLIWOC-EU (v2.1 stvno), 2003",'subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})\

airports = data.airports.url

def add_points(layer1,k):
    points = alt.Chart(fc.iloc[k:k+4999])\
        .mark_line(size=route_sz,color=colors['eco-purple']).encode(
        longitude='LON:Q',
        latitude='LAT:Q',
        opacity=alt.Opacity('ID:Q',scale=alt.Scale(range=[route_op,route_op]),legend=None),
        color=alt.Color('C1:N',scale=alt.Scale(range=[colors['eco-turquiose'],colors['eco-orange'],colors['eco-purple']]),legend=None)
    )
    return layer1+points

tdx=20
label1=alt.Chart(pd.DataFrame([{'x':0,'y':0,'t':'British'}])).mark_text(fontSize=15,color=colors['eco-purple']+'dd',yOffset=-180,xOffset=-200+tdx,align='left')\
    .encode(x=alt.X('x:Q',axis=None),y=alt.Y('y:Q',axis=None),text='t:N')
label2=alt.Chart(pd.DataFrame([{'x':0,'y':0,'t':'Dutch'}])).mark_text(fontSize=15,color=colors['eco-orange']+'dd',yOffset=-180,xOffset=-64+tdx,align='left')\
    .encode(x=alt.X('x:Q',axis=None),y=alt.Y('y:Q',axis=None),text='t:N')
label3=alt.Chart(pd.DataFrame([{'x':0,'y':0,'t':'Spanish'}])).mark_text(fontSize=15,color=colors['eco-turquiose']+'dd',yOffset=-180,xOffset=-150+tdx,align='left')\
    .encode(x=alt.X('x:Q',axis=None),y=alt.Y('y:Q',axis=None),text='t:N')
label4=alt.Chart(pd.DataFrame([{'x':0,'y':0,'t':',                and             shipping routes 1677 - 1855'}])).mark_text(fontSize=15,color=colors['eco-gray']+'dd',
                                                                                                 yOffset=-180,xOffset=-157+tdx,align='left')\
    .encode(x=alt.X('x:Q',axis=None),y=alt.Y('y:Q',axis=None),text='t:N')
layer1=(background + label1+ label2+ label3+ label4)

layer1=add_points(layer1,0)
for i in range(len(df)//5000):
    layer1=add_points(layer1,i*5000)

layer1=layer1.configure(font='Circular Std Book')\
    .configure_view(stroke=None,discreteWidth=600,discreteHeight=400,continuousWidth=600,continuousHeight=400)

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.display()

fig7-2_map_current_shipping



alt.LayerChart(...)

alt.LayerChart(...)

## Map 2

In [31]:
readme, f, fc = save(df,"fig7-2_map_current_shipping",LOCAL)

In [100]:
colors['eco-background']

'#122B39'

In [183]:
route_op=0.1
route_sz=0.6
background=alt.layer(
    alt.Chart(sphere).mark_geoshape(fill='#cccddd'),
    alt.Chart(source).mark_geoshape(fill='#eeeeee', stroke='#cccddd',opacity=1)
).project(
    'naturalEarth1'
).properties(title={'text':" ",'color':colors['eco-gray']+'dd','offset':-415,
              'subtitle':"Source: Adam Symington/PythonMaps based on data from World Bank & IMF, 2021",'subtitlePadding':360,
               'subtitleFontSize':11,'subtitleColor':colors['eco-gray']+'bb','fontSize':15})\

tdx=20
label1=alt.Chart(pd.DataFrame([{'x':0,'y':0,'t':'Global shipping routes in 2021'}])).mark_text(fontSize=15,color=colors['eco-purple']+'dd',yOffset=-180,align='center')\
    .encode(x=alt.X('x:Q',axis=None),y=alt.Y('y:Q',axis=None),text='t:N')
layer1=(background 
        + label1
       )

logo=alt.Chart(pd.DataFrame([{"x": 0, "y": 0, "img": "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/magazine/issue-3/raw/shipping-dark.png"}]))\
    .mark_image(width=680,height=460,yOffset=1,opacity=0.6,xOffset=0).encode(x=alt.X('x:Q'),
            y=alt.Y('y:Q'),url='img:N')

layer1=(layer1+logo).configure(font='Circular Std Book')\
    .configure_view(stroke=None,discreteWidth=600,discreteHeight=400,continuousWidth=600,continuousHeight=400)

if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    layer2=dark(f)
    layer2=layer2.to_dict()
    layer2['layer'][2]['mark']['color']=colors['eco-light-blue']
    layer2['layer'][3]['mark']['opacity']=0.9
    layer2=alt.Chart().from_dict(layer2)
    layer2.save("visualisation/" + f + "_dark.json")
    layer2.save("visualisation/" + f + "_dark.svg")
    layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "a").write(readme)

print(f+'\n')
layer1.display()
if SAVE:
    layer2.display()
    
# force display dark
if DARK and not SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2=layer2.to_dict()
    layer2['layer'][2]['mark']['color']=colors['eco-light-blue']
    layer2['layer'][3]['mark']['opacity']=0.9
    layer2=alt.Chart().from_dict(layer2)
    layer2['config']
    layer2.display()

fig7-2_map_current_shipping



alt.LayerChart(...)

alt.LayerChart(...)

# Article 13
What policies might Smith advocate today?

# Article 16
Rebalancing the economy

# Article 20
Gender gaps in paid and unpaid work